Project: Echoes of Power
=====

In this problem set, you will use iPython notebook and various python tools to read data and analyze it.

We will use data from the paper 

In [1]:
%pylab inline



Populating the interactive namespace from numpy and matplotlib


In [2]:
utterances = {}
def load_data():
    with open('wikipedia.talkpages.conversations.txt', "r") as f:
        for line in f:
            split = line.split("+++$+++")
#             print len(split)
            try:
                utterances[split[0].strip()] = {"user_id": split[1].strip(),
                                        "talkpage_user": split[2].strip(), 
                                        "conversation_root": split[3].strip(),
                                        "reply_to": split[4].strip(),
                                        "timestamp": split[5].strip(),
                                        "timestamp_unix": split[6].strip(),
                                        "text": split[6].strip(),
                                        "raw_text": split[7].strip()
                                        }
            except IndexError:
                pass
load_data()


In [3]:
# utterances.keys()

In [4]:
conversations = {}
for u_id, utter in utterances.iteritems():
    user_id = utter["user_id"]
    reply_id = utter.get("reply_to")
#     print utterances.get(reply_id)
#     print reply_id
    root_conversation = utter["conversation_root"]
    if root_conversation == u_id:
        continue
    if conversations.get(root_conversation) == None:
        conversations[root_conversation] = [u_id]
    else:
        conversations[root_conversation].append(u_id)
        
        
#     if reply_id and utterances.get(reply_id):
#         reply_user_id = utterances[reply_id]["user_id"]
#         if(conversations.get((user_id, reply_user_id)) == None):
#             conversations[utter["conversation_root"]] = [reply_id, u_id]
#         else:
#             conversations[(user_id, reply_user_id)].append(reply_id)
#             conversations[(user_id, reply_user_id)].append(u_id)
conversations
print len(conversations.keys())

125292


In [5]:
count = 0.0
for i in conversations.keys():
    if utterances[i]["user_id"] == utterances[i]["talkpage_user"]:
        count += 1
print count/125292

0.0426763081442


In [6]:
cnt = 0
for i in utterances.keys():
    if(utterances[i]["reply_to"] == i):
        cnt += 1
#     print utterances[i]["reply_to"]
#     pass
cnt

0

In [35]:

#'577840': ['577843', '577842', '577841', '577844']]
print utterances['577843']
print (utterances['577842']['reply_to'])
print utterances['577841']
# print utterances['577844']['reply_to']
print utterances['577840']

{'conversation_root': '577840', 'user_id': 'Zanimum', 'talkpage_user': 'Zanimum', 'timestamp_unix': '1.179627540E09', 'reply_to': '577842', 'timestamp': '2007-05-19 19:19:00', 'text': '1.179627540E09', 'raw_text': "No, I'll keep it. :) Just wanted to make sure you knew I didn't click the camera myself. Anyway, thanks for noticing my efforts.  --"}
577841
{'conversation_root': '577840', 'user_id': 'Zanimum', 'talkpage_user': 'Zanimum', 'timestamp_unix': '1.179626880E09', 'reply_to': '577840', 'timestamp': '2007-05-19 19:08:00', 'text': '1.179626880E09', 'raw_text': '[Blush] I don\'t know if I do... they were taken by other volunteer photographers, that I \\"commissioned\\". I\'ve been aranging as many photo shoots as possible, to get this type of image.  --'}
{'conversation_root': '577840', 'user_id': 'QuasyBoy', 'talkpage_user': 'Zanimum', 'timestamp_unix': '1.179608280E09', 'reply_to': 'initial_post', 'timestamp': '2007-05-19 13:58:00', 'text': '1.179608280E09', 'raw_text': '|style=\\

In [16]:
def get_other_user(conversation_list, root_user):
    for i in conversation_list:
        other_user = utterances[i]["user_id"]
        if utterances[i]["user_id"] != root_user and other_user != "":
            return other_user

In [25]:
# conversations

In [23]:
conv_list = ['445339','445338','445337','445336','445335','445344','445345','445342','445343','445340','445341']
# '228054': ['228055', '228056']
conv_list = ['228054','228055', '228056']
conv_list = ['320591', '320597', '320595', '320594', '320593', '320592', '320596']

class Node:
    def __init__(self, u_id):
        self.u_id = u_id
        self.child = None
        self.parent = None
#     def add_child(self, child_node=None, parent_node=None):
#         self.child = child_node
#         self.parent = parent_node
#         return True
def get_root(node_list, start_node):
    if start_node.parent == None:
        return start_node
    else:
        parent = start_node.parent
        return get_root(node_list, node_list[parent])


def compute_conversation_hierarchy(conv_list):
    node_list = {}
    for i in conv_list:
        node_list[i] = Node(i)
    for i in conv_list:
        reply_to = utterances[i]["reply_to"]
        if reply_to != '-1' and reply_to != "initial_post":
            node_list[i].parent = reply_to
            node_list[reply_to].child = i
    root = get_root(node_list, node_list.values()[0])
    new_list = [root.u_id]
    cur = root
    while(len(new_list) < len(node_list) and cur.child != None):
        cur = node_list[cur.child]
        new_list.append(cur.u_id)
        
    return new_list
print compute_conversation_hierarchy(conv_list)

#     for i in node_list.values():
#         print i.u_id
#         print "its child is %s" % i.child
#         print "its parent is %s" % i.parent

['320591', '320592', '320593', '320594', '320595', '320596', '320597']


In [24]:
final_conversations = {}
import copy
for i, j in conversations.iteritems():
    conv_list = copy.deepcopy(j)
    conv_list.insert(0, i)
    conv_hierarchy = compute_conversation_hierarchy(conv_list)
    B_user = utterances[i]["talkpage_user"]
    A_user = utterances[i]["user_id"]
    if final_conversations.get((A_user, B_user)):
        final_conversations[(A_user, B_user)].append(conv_hierarchy)
    else:
        final_conversations[(A_user, B_user)] = [conv_hierarchy]
#     break
    
print final_conversations
    

{('WikiuserNI', 'WikiuserNI'): [['212659', '212666']], ('Jmabel', 'Error'): [['124771', '124772']], ('P-antibody', 'Jayron32'): [['355689', '355692', '355693']], ('Damifb', 'Shirahadasha'): [['378504', '378505'], ['378507']], ('Voice of All(MTG)', 'MONGO'): [['572268', '572269'], ['572345', '572346']], ('Jj137', 'Andonic'): [['24034', '24035'], ['397524', '397525']], ('Poeloq', 'Jared Preston'): [['179583', '179584']], ('122.107.11.230', 'MECU'): [['588674', '588675', '588676']], ('Telcourbanio', 'JoJan'): [['553935']], ('Emhale', 'TimVickers'): [['543557', '543558']], ('Neschek', 'JRM'): [['517516', '517517']], ('Daedalus969', 'Carlossuarez46'): [['609106', '609107', '609108', '609109'], ['541414', '541415', '541416', '541417']], ('Jonathan Logan', 'Stormbay'): [['60699', '60700']], ('HJ Mitchell', 'Clarityfiend'): [['174902', '174903', '174904']], ('WarthogDemon', 'Ckatz'): [['519055', '519056']], ('Enigmaman', 'OhanaUnited'): [['555792', '555793', '555794'], ['555820', '555823', '55

In [23]:
def append_to_left_of(item, li, item_to_insert, conv_list):
    if(item in li):
        index= li.index(item)
        li.insert(index, item_to_insert)
        conv_list.remove

def make_conv_list(conv_list):
    cur_conv = [conv_list[0]]
    for c in range(1,len(conv_list)):
        reply_to = utterances[c]["reply_to"]
        

conv_list = ['445339','445338','445337','445336','445335','445344','445345','445342','445343','445340','445341']
def get_ordered_conversation(conv_list):
    temp = []
    while(len(conv_list) > 0):
        conv_list[]
        make_conv_list(conv_list)
    for c in conv_list:
        reply_to = utterances[c]["reply_to"]
        append_to_left_of
        print reply_to
get_ordered_conversation(conv_list)

445338
445337
445336
445335
445334
445343
445344
-1
445341
-1
445334


In [ ]:
conv_left = []


In [17]:
conversation_threads = {}
for i, v in conversations.iteritems():
    root_user = utterances[i]["user_id"]
    other_user = get_other_user(v, root_user)
    conversation_threads[(root_user, other_user)] = get_ordered_conversation(v)
conversation_threads

{('Jareth', None): ['597872'],
 ('Jmabel', 'Error'): ['124772'],
 ('Alensha', 'Enric Naval'): ['456970', '456969'],
 ('RaviC', 'Nbahn'): ['469643', '469642'],
 ('VascoAmaral', 'Waldir'): ['444329', '444328'],
 ('Keeper76', 'Gwynand'): ['445339',
  '445338',
  '445337',
  '445336',
  '445335',
  '445344',
  '445345',
  '445342',
  '445343',
  '445340',
  '445341'],
 ('Voice of All(MTG)', 'MONGO'): ['572269'],
 ('Gadget850', None): ['505311', '505310', '505312'],
 ('Rosepuff12', 'Acalamari'): ['583488',
  '583489',
  '583484',
  '583485',
  '583486',
  '583487'],
 ('LaraBot', 'Courcelles'): ['35810'],
 ('Telcourbanio', 'JoJan'): ['553936'],
 ('P-antibody', 'Jayron32'): ['355690', '355691', '355692', '355693'],
 ('Tuleytula', 'Carcharoth'): ['474242'],
 ('Zachariel', 'William M. Connolley'): ['102789'],
 ('HonouraryMix', None): ['66115'],
 ('Jonathan Logan', 'Stormbay'): ['60700'],
 ('WickerGuy', 'Jerome Kohl'): ['89394'],
 ('Grandmasterka', 'Blnguyen'): ['359015'],
 ('RepublicanJacobite'